In [1]:
from ase_interface import ANIENS
from ase_interface import ensemblemolecule_multigpu
from ase_interface import ensemblemolecule

import pyNeuroChem as pync
#import pyaniasetools as pya
import hdnntools as hdt

import numpy as np
import  ase

import time

import os
os.environ["OMP_NUM_THREADS"] = "8"

import  ase
from ase.md.langevin import Langevin
from ase.md.verlet import VelocityVerlet
from ase.io.trajectory import Trajectory
from ase import units

from ase.optimize.fire import FIRE as QuasiNewton
from ase.optimize import LBFGS

from ase.md.nvtberendsen import NVTBerendsen
from ase.md import MDLogger

from ase.io import read, write

from ase.parallel import world

van Der Waals correction will be unavailable. Please install ased3


In [2]:
dir = '/nh/nest/u/jsmith/scratch/Research/carbon_nano_tube/MD/functionalized_2_justin/11_0/o2/'

fname = 'geometry'

# Molecule file
molfile = dir + fname + '.xyz'

# Dynamics file
xyzfile = dir + 'mdcrd.xyz'

# Trajectory file
trajfile = dir + 'traj.dat'

# Optimized structure out:
optfile = dir + 'opt_' +  fname +'.xyz'

dt = 0.5
rt = 1.0 # run time in ns
st = 50 # store step
C = 0.0001 # Optimization convergence

ntdir = '/nh/nest/u/jsmith/scratch/Research/ccsd_extrapolation/final_train_models_3/ani-1x_dft_x8ens/'
cns = ntdir + 'rHCNO-5.2R_16-3.5A_a4-8.params'
sae = ntdir + 'sae_linfit.dat'
nnf = ntdir + 'train'
Nn = 8

In [3]:
steps = int((rt * 1000 * 1000) / dt)
print(steps)

2000000


In [4]:
#tvec = np.loadtxt(dir+'/'+fname+'.tvec',dtype=str)
#tvec = np.array(tvec[:,1:],dtype=np.float64)

In [5]:
tvec

array([[18.617822,  0.      ,  0.      ],
       [ 0.      , 18.617822,  0.      ],
       [ 0.      ,  0.      , 21.315   ]])

In [6]:
# Load molecule
mol = read(molfile)
#L=40.0
# mol.set_cell(([[100.0, 0, 0],
#                 [0, 35.0, 0],
#                 [0, 0, 35.0]]))

mol.set_cell((tvec))


mol.set_pbc((True, True, True))
#mol.set_pbc((False, False, False))

# Set NC
aens = ensemblemolecule(cns, sae, nnf, Nn, 0)
#aens = ensemblemolecule(cns, sae, nnf, Nn, 1)

# Set ANI calculator
mol.set_calculator(ANIENS(aens))

s_time = time.time()
E = mol.get_potential_energy()
F = mol.get_forces()
print('Total time:',time.time()-s_time)

print(E)

spc = mol.get_chemical_symbols()
print(len(spc))

Total time: 0.048006296157836914
-230140.50626077325
221


In [7]:
# Optimize molecule
start_time = time.time()
dyn = LBFGS(mol)
dyn.run(fmax=C,steps=3000)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

# Save optimized mol
spc = mol.get_chemical_symbols()
pos = mol.get_positions(wrap=False).reshape(1,len(spc),3)


hdt.writexyzfile(optfile, pos, spc)

       Step     Time          Energy         fmax
LBFGS:    0 16:59:13  -230140.506261       10.1840
LBFGS:    1 16:59:13  -230141.324813        5.6387
LBFGS:    2 16:59:13  -230142.157898        3.8796
LBFGS:    3 16:59:13  -230142.834076        2.5795
LBFGS:    4 16:59:13  -230143.499746        2.1357
LBFGS:    5 16:59:13  -230144.161561        2.0559
LBFGS:    6 16:59:13  -230144.833584        2.2002
LBFGS:    7 16:59:13  -230145.492302        2.2590
LBFGS:    8 16:59:13  -230146.132711        2.2092
LBFGS:    9 16:59:13  -230146.711825        2.1274
LBFGS:   10 16:59:13  -230147.256699        2.0257
LBFGS:   11 16:59:13  -230147.753316        1.9038
LBFGS:   12 16:59:13  -230148.188396        1.8383
LBFGS:   13 16:59:13  -230148.526124        1.8486
LBFGS:   14 16:59:13  -230148.748608        1.3547
LBFGS:   15 16:59:13  -230148.836503        0.9714
LBFGS:   16 16:59:13  -230148.885563        0.8142
LBFGS:   17 16:59:13  -230148.915739        0.2914
LBFGS:   18 16:59:13  -230148.92

LBFGS:  160 16:59:15  -230149.044987        0.0104
LBFGS:  161 16:59:15  -230149.045080        0.0101
LBFGS:  162 16:59:15  -230149.045152        0.0082
LBFGS:  163 16:59:15  -230149.045244        0.0093
LBFGS:  164 16:59:15  -230149.045307        0.0095
LBFGS:  165 16:59:15  -230149.045389        0.0086
LBFGS:  166 16:59:15  -230149.045441        0.0071
LBFGS:  167 16:59:15  -230149.045499        0.0061
LBFGS:  168 16:59:15  -230149.045532        0.0065
LBFGS:  169 16:59:15  -230149.045551        0.0063
LBFGS:  170 16:59:15  -230149.045596        0.0060
LBFGS:  171 16:59:15  -230149.045620        0.0058
LBFGS:  172 16:59:15  -230149.045625        0.0048
LBFGS:  173 16:59:15  -230149.045658        0.0041
LBFGS:  174 16:59:15  -230149.045669        0.0034
LBFGS:  175 16:59:15  -230149.045684        0.0032
LBFGS:  176 16:59:15  -230149.045695        0.0026
LBFGS:  177 16:59:15  -230149.045700        0.0028
LBFGS:  178 16:59:15  -230149.045706        0.0024
LBFGS:  179 16:59:15  -230149.0

In [8]:
# We want to run MD with constant energy using the VelocityVerlet algorithm.
#dyn = NVTBerendsen(mol, 1 * units.fs, 100.0, taut=1.0*1000*units.fs)
# coefficient to 0.04 atomic units.
dyn = Langevin(mol, dt * units.fs, 1.0 * units.kB, 0.04)

In [9]:
# Open MD output
mdcrd = open(xyzfile,'w')

# Open MD output
traj = open(trajfile,'w')

# Define the printer
def storeenergy(a=mol, d=dyn, b=mdcrd, t=traj):  # store a reference to atoms in the definition.
    """Function to print the potential, kinetic and total energy."""
    epot = a.get_potential_energy() / len(a)
    ekin = a.get_kinetic_energy() / len(a)

    stddev =  hdt.evtokcal*a.calc.stddev
    Fstddev =  hdt.evtokcal*a.calc.Fstddev

    t.write(str(d.get_number_of_steps()) + ' ' + str(ekin / (1.5 * units.kB)) + ' ' + str(epot) + ' ' + str(ekin) + ' ' + str(epot+ekin) + ' ' + str(stddev) + '\n')
    b.write(str(len(a)) + '\n' + str(ekin / (1.5 * units.kB)) + ' Step: ' + str(d.get_number_of_steps()) + '\n')
    c = a.get_positions(wrap=False)
    for j, i in zip(a, c):
        b.write(str(j.symbol) + ' ' + str(i[0]) + ' ' + str(i[1]) + ' ' + str(i[2]) + '\n')

    print('Step: %d Energy per atom: Epot = %.3f  Ekin = %.3f (T=%.3fK)  '
          'Etot = %.6f Esig = %.3f Fsig = %.3f' % (d.get_number_of_steps(), epot, ekin, ekin / (1.5 * units.kB), epot + ekin, stddev,Fstddev))
    
# Set the printer
dyn.attach(storeenergy, interval=st)

In [10]:
start_time = time.time()
dyn.set_temperature(300. * units.kB)
dyn.run(steps)
print('[ANI Total time:', time.time() - start_time, 'seconds]')

Step: 50 Energy per atom: Epot = -1041.395  Ekin = 0.004 (T=31.248K)  Etot = -1041.391026 Esig = 62.554 Fsig = 0.301
Step: 100 Energy per atom: Epot = -1041.392  Ekin = 0.007 (T=52.021K)  Etot = -1041.384864 Esig = 63.070 Fsig = 0.346
Step: 150 Energy per atom: Epot = -1041.388  Ekin = 0.010 (T=74.937K)  Etot = -1041.378465 Esig = 63.373 Fsig = 0.376
Step: 200 Energy per atom: Epot = -1041.385  Ekin = 0.013 (T=101.582K)  Etot = -1041.371836 Esig = 64.065 Fsig = 0.394
Step: 250 Energy per atom: Epot = -1041.382  Ekin = 0.016 (T=122.706K)  Etot = -1041.365948 Esig = 64.355 Fsig = 0.414
Step: 300 Energy per atom: Epot = -1041.381  Ekin = 0.019 (T=150.426K)  Etot = -1041.361711 Esig = 64.100 Fsig = 0.431
Step: 350 Energy per atom: Epot = -1041.378  Ekin = 0.020 (T=151.415K)  Etot = -1041.358263 Esig = 64.340 Fsig = 0.430
Step: 400 Energy per atom: Epot = -1041.377  Ekin = 0.022 (T=170.830K)  Etot = -1041.355078 Esig = 65.492 Fsig = 0.464
Step: 450 Energy per atom: Epot = -1041.373  Ekin = 

Step: 3500 Energy per atom: Epot = -1041.361  Ekin = 0.038 (T=291.832K)  Etot = -1041.323354 Esig = 64.750 Fsig = 0.518
Step: 3550 Energy per atom: Epot = -1041.360  Ekin = 0.035 (T=271.483K)  Etot = -1041.324587 Esig = 65.024 Fsig = 0.511
Step: 3600 Energy per atom: Epot = -1041.361  Ekin = 0.037 (T=285.384K)  Etot = -1041.323690 Esig = 64.690 Fsig = 0.514
Step: 3650 Energy per atom: Epot = -1041.363  Ekin = 0.040 (T=306.424K)  Etot = -1041.323190 Esig = 65.346 Fsig = 0.513
Step: 3700 Energy per atom: Epot = -1041.360  Ekin = 0.039 (T=305.140K)  Etot = -1041.320832 Esig = 64.378 Fsig = 0.528
Step: 3750 Energy per atom: Epot = -1041.358  Ekin = 0.038 (T=292.957K)  Etot = -1041.320057 Esig = 65.679 Fsig = 0.536
Step: 3800 Energy per atom: Epot = -1041.359  Ekin = 0.039 (T=305.233K)  Etot = -1041.319783 Esig = 66.450 Fsig = 0.519
Step: 3850 Energy per atom: Epot = -1041.361  Ekin = 0.042 (T=321.098K)  Etot = -1041.319202 Esig = 64.245 Fsig = 0.494
Step: 3900 Energy per atom: Epot = -1041

Step: 6950 Energy per atom: Epot = -1041.361  Ekin = 0.037 (T=287.591K)  Etot = -1041.323510 Esig = 65.266 Fsig = 0.505
Step: 7000 Energy per atom: Epot = -1041.360  Ekin = 0.036 (T=282.138K)  Etot = -1041.323090 Esig = 65.899 Fsig = 0.517
Step: 7050 Energy per atom: Epot = -1041.360  Ekin = 0.037 (T=286.962K)  Etot = -1041.322410 Esig = 65.553 Fsig = 0.543
Step: 7100 Energy per atom: Epot = -1041.360  Ekin = 0.039 (T=305.191K)  Etot = -1041.320292 Esig = 66.662 Fsig = 0.530
Step: 7150 Energy per atom: Epot = -1041.359  Ekin = 0.040 (T=309.585K)  Etot = -1041.318930 Esig = 66.049 Fsig = 0.522
Step: 7200 Energy per atom: Epot = -1041.361  Ekin = 0.040 (T=308.207K)  Etot = -1041.320721 Esig = 66.131 Fsig = 0.508
Step: 7250 Energy per atom: Epot = -1041.357  Ekin = 0.038 (T=290.253K)  Etot = -1041.319425 Esig = 64.096 Fsig = 0.520
Step: 7300 Energy per atom: Epot = -1041.358  Ekin = 0.038 (T=295.430K)  Etot = -1041.320156 Esig = 66.008 Fsig = 0.528
Step: 7350 Energy per atom: Epot = -1041

Step: 10400 Energy per atom: Epot = -1041.358  Ekin = 0.038 (T=296.831K)  Etot = -1041.319921 Esig = 64.272 Fsig = 0.513
Step: 10450 Energy per atom: Epot = -1041.357  Ekin = 0.039 (T=304.128K)  Etot = -1041.318091 Esig = 63.782 Fsig = 0.509
Step: 10500 Energy per atom: Epot = -1041.359  Ekin = 0.040 (T=308.601K)  Etot = -1041.319303 Esig = 65.053 Fsig = 0.502
Step: 10550 Energy per atom: Epot = -1041.359  Ekin = 0.039 (T=303.619K)  Etot = -1041.319790 Esig = 65.684 Fsig = 0.499
Step: 10600 Energy per atom: Epot = -1041.359  Ekin = 0.041 (T=319.518K)  Etot = -1041.317564 Esig = 64.445 Fsig = 0.525
Step: 10650 Energy per atom: Epot = -1041.359  Ekin = 0.041 (T=313.601K)  Etot = -1041.318146 Esig = 65.273 Fsig = 0.514
Step: 10700 Energy per atom: Epot = -1041.359  Ekin = 0.040 (T=312.391K)  Etot = -1041.318749 Esig = 64.758 Fsig = 0.494
Step: 10750 Energy per atom: Epot = -1041.356  Ekin = 0.037 (T=284.216K)  Etot = -1041.319163 Esig = 64.917 Fsig = 0.496
Step: 10800 Energy per atom: Epo

Step: 13800 Energy per atom: Epot = -1041.360  Ekin = 0.036 (T=281.574K)  Etot = -1041.323806 Esig = 65.255 Fsig = 0.510
Step: 13850 Energy per atom: Epot = -1041.362  Ekin = 0.039 (T=298.302K)  Etot = -1041.323620 Esig = 65.689 Fsig = 0.501
Step: 13900 Energy per atom: Epot = -1041.360  Ekin = 0.037 (T=289.521K)  Etot = -1041.323007 Esig = 64.966 Fsig = 0.511
Step: 13950 Energy per atom: Epot = -1041.362  Ekin = 0.038 (T=295.314K)  Etot = -1041.324241 Esig = 64.856 Fsig = 0.513
Step: 14000 Energy per atom: Epot = -1041.359  Ekin = 0.036 (T=277.020K)  Etot = -1041.323688 Esig = 64.671 Fsig = 0.502
Step: 14050 Energy per atom: Epot = -1041.361  Ekin = 0.039 (T=300.879K)  Etot = -1041.322014 Esig = 65.207 Fsig = 0.504
Step: 14100 Energy per atom: Epot = -1041.358  Ekin = 0.036 (T=278.724K)  Etot = -1041.322072 Esig = 64.959 Fsig = 0.507
Step: 14150 Energy per atom: Epot = -1041.357  Ekin = 0.034 (T=263.170K)  Etot = -1041.322714 Esig = 65.128 Fsig = 0.522
Step: 14200 Energy per atom: Epo

...

Step: 1984700 Energy per atom: Epot = -1041.361  Ekin = 0.037 (T=285.594K)  Etot = -1041.324217 Esig = 66.201 Fsig = 0.532
Step: 1984750 Energy per atom: Epot = -1041.364  Ekin = 0.037 (T=288.508K)  Etot = -1041.326439 Esig = 65.407 Fsig = 0.496
Step: 1984800 Energy per atom: Epot = -1041.362  Ekin = 0.035 (T=273.539K)  Etot = -1041.326905 Esig = 64.823 Fsig = 0.496
Step: 1984850 Energy per atom: Epot = -1041.362  Ekin = 0.034 (T=264.572K)  Etot = -1041.327881 Esig = 65.630 Fsig = 0.497
Step: 1984900 Energy per atom: Epot = -1041.365  Ekin = 0.037 (T=290.109K)  Etot = -1041.327338 Esig = 65.164 Fsig = 0.512
Step: 1984950 Energy per atom: Epot = -1041.363  Ekin = 0.035 (T=274.070K)  Etot = -1041.328013 Esig = 65.406 Fsig = 0.512
Step: 1985000 Energy per atom: Epot = -1041.363  Ekin = 0.037 (T=286.953K)  Etot = -1041.325615 Esig = 64.872 Fsig = 0.507
Step: 1985050 Energy per atom: Epot = -1041.362  Ekin = 0.038 (T=293.104K)  Etot = -1041.324513 Esig = 65.139 Fsig = 0.497
Step: 1985100 En

Step: 1988050 Energy per atom: Epot = -1041.362  Ekin = 0.039 (T=298.981K)  Etot = -1041.323516 Esig = 64.781 Fsig = 0.490
Step: 1988100 Energy per atom: Epot = -1041.364  Ekin = 0.041 (T=313.323K)  Etot = -1041.323758 Esig = 65.458 Fsig = 0.493
Step: 1988150 Energy per atom: Epot = -1041.364  Ekin = 0.041 (T=320.748K)  Etot = -1041.322588 Esig = 65.945 Fsig = 0.471
Step: 1988200 Energy per atom: Epot = -1041.362  Ekin = 0.040 (T=305.968K)  Etot = -1041.322463 Esig = 66.163 Fsig = 0.489
Step: 1988250 Energy per atom: Epot = -1041.359  Ekin = 0.036 (T=276.512K)  Etot = -1041.323321 Esig = 65.190 Fsig = 0.492
Step: 1988300 Energy per atom: Epot = -1041.362  Ekin = 0.041 (T=315.770K)  Etot = -1041.321392 Esig = 65.399 Fsig = 0.493
Step: 1988350 Energy per atom: Epot = -1041.359  Ekin = 0.038 (T=291.435K)  Etot = -1041.321112 Esig = 65.328 Fsig = 0.514
Step: 1988400 Energy per atom: Epot = -1041.358  Ekin = 0.039 (T=299.892K)  Etot = -1041.319713 Esig = 65.039 Fsig = 0.501
Step: 1988450 En

Step: 1991400 Energy per atom: Epot = -1041.359  Ekin = 0.038 (T=295.718K)  Etot = -1041.321005 Esig = 65.827 Fsig = 0.534
Step: 1991450 Energy per atom: Epot = -1041.360  Ekin = 0.039 (T=300.721K)  Etot = -1041.321084 Esig = 66.613 Fsig = 0.520
Step: 1991500 Energy per atom: Epot = -1041.360  Ekin = 0.038 (T=293.419K)  Etot = -1041.321853 Esig = 65.943 Fsig = 0.515
Step: 1991550 Energy per atom: Epot = -1041.361  Ekin = 0.038 (T=291.512K)  Etot = -1041.323174 Esig = 65.285 Fsig = 0.523
Step: 1991600 Energy per atom: Epot = -1041.362  Ekin = 0.039 (T=301.278K)  Etot = -1041.323377 Esig = 65.613 Fsig = 0.513
Step: 1991650 Energy per atom: Epot = -1041.363  Ekin = 0.039 (T=303.314K)  Etot = -1041.324252 Esig = 64.884 Fsig = 0.506
Step: 1991700 Energy per atom: Epot = -1041.361  Ekin = 0.037 (T=288.422K)  Etot = -1041.324129 Esig = 65.736 Fsig = 0.508
Step: 1991750 Energy per atom: Epot = -1041.363  Ekin = 0.038 (T=293.165K)  Etot = -1041.324628 Esig = 66.141 Fsig = 0.496
Step: 1991800 En

Step: 1994750 Energy per atom: Epot = -1041.364  Ekin = 0.039 (T=301.879K)  Etot = -1041.324680 Esig = 65.651 Fsig = 0.498
Step: 1994800 Energy per atom: Epot = -1041.362  Ekin = 0.039 (T=298.289K)  Etot = -1041.323008 Esig = 66.334 Fsig = 0.523
Step: 1994850 Energy per atom: Epot = -1041.362  Ekin = 0.039 (T=299.933K)  Etot = -1041.322947 Esig = 65.128 Fsig = 0.528
Step: 1994900 Energy per atom: Epot = -1041.360  Ekin = 0.040 (T=307.956K)  Etot = -1041.320630 Esig = 65.502 Fsig = 0.521
Step: 1994950 Energy per atom: Epot = -1041.363  Ekin = 0.040 (T=312.702K)  Etot = -1041.322081 Esig = 66.324 Fsig = 0.486
Step: 1995000 Energy per atom: Epot = -1041.359  Ekin = 0.038 (T=297.287K)  Etot = -1041.321054 Esig = 67.147 Fsig = 0.516
Step: 1995050 Energy per atom: Epot = -1041.358  Ekin = 0.038 (T=294.577K)  Etot = -1041.319608 Esig = 64.449 Fsig = 0.541
Step: 1995100 Energy per atom: Epot = -1041.358  Ekin = 0.039 (T=298.076K)  Etot = -1041.319440 Esig = 65.993 Fsig = 0.535
Step: 1995150 En

Step: 1998100 Energy per atom: Epot = -1041.361  Ekin = 0.040 (T=312.866K)  Etot = -1041.320938 Esig = 64.409 Fsig = 0.530
Step: 1998150 Energy per atom: Epot = -1041.359  Ekin = 0.037 (T=289.537K)  Etot = -1041.321933 Esig = 64.625 Fsig = 0.510
Step: 1998200 Energy per atom: Epot = -1041.362  Ekin = 0.041 (T=316.070K)  Etot = -1041.320969 Esig = 66.676 Fsig = 0.506
Step: 1998250 Energy per atom: Epot = -1041.360  Ekin = 0.038 (T=292.406K)  Etot = -1041.322396 Esig = 66.502 Fsig = 0.527
Step: 1998300 Energy per atom: Epot = -1041.359  Ekin = 0.039 (T=298.473K)  Etot = -1041.320879 Esig = 65.130 Fsig = 0.549
Step: 1998350 Energy per atom: Epot = -1041.358  Ekin = 0.038 (T=294.685K)  Etot = -1041.320273 Esig = 65.560 Fsig = 0.528
Step: 1998400 Energy per atom: Epot = -1041.359  Ekin = 0.038 (T=290.234K)  Etot = -1041.321379 Esig = 65.054 Fsig = 0.518
Step: 1998450 Energy per atom: Epot = -1041.360  Ekin = 0.038 (T=293.210K)  Etot = -1041.322163 Esig = 65.706 Fsig = 0.493
Step: 1998500 En